In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
import json
import pandas as pd
import numpy as np
import torch

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/arxiv/arxiv-metadata-oai-snapshot.json


In [2]:
pip install transformers

Note: you may need to restart the kernel to use updated packages.


In [3]:
pip install sentence-transformers

     |████████████████████████████████| 78 kB 929 kB/s            
  Preparing metadata (setup.py) ... - done
  Created wheel for sentence-transformers: filename=sentence_transformers-2.1.0-py3-none-any.whl size=121000 sha256=2595703bdcdf6dabbef088531d99111846b68c059a748a683d3befe7e54e495d
  Stored in directory: /root/.cache/pip/wheels/90/f0/bb/ed1add84da70092ea526466eadc2bfb197c4bcb8d4fa5f7bad
Successfully built sentence-transformers
Note: you may need to restart the kernel to use updated packages.


In [4]:
from sentence_transformers import SentenceTransformer, util
model = SentenceTransformer('allenai/scibert_scivocab_uncased')
model.max_seq_length = 512

Downloading:   0%|          | 0.00/437 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/1.11k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/385 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/442M [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/228k [00:00<?, ?B/s]

Some weights of the model checkpoint at /root/.cache/torch/sentence_transformers/allenai_scibert_scivocab_uncased were not used when initializing BertModel: ['cls.predictions.decoder.bias', 'cls.seq_relationship.bias', 'cls.predictions.decoder.weight', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.bias', 'cls.seq_relationship.weight', 'cls.predictions.transform.dense.bias', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.transform.dense.weight']
- This IS expected if you are initializing BertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


In [5]:
data_file = '../input/arxiv/arxiv-metadata-oai-snapshot.json'

In [6]:
def get_metadata():
    with open(data_file, 'r') as f:
        for line in f:
            yield line

In [7]:
metadata = get_metadata()
ids = []
titles = []
abstracts = []
categories = []
for paper in metadata:
    metaDict = json.loads(paper)
    try:
        try:
            year = int(metaDict['journal-ref'][-4:])    ### Example Format: "Phys.Rev.D76:013009,2007"
        except:
            year = int(metaDict['journal-ref'][-5:-1])    ### Example Format: "Phys.Rev.D76:013009,(2007)"
        if(year == 2020):
            ids.append(metaDict['id'])
            titles.append(metaDict['title'])
            abstracts.append(metaDict['abstract'])
            categories.append(metaDict['categories'])
    except:
        pass

In [8]:
df = pd.DataFrame({'id' : ids,'title' : titles,'abstract' : abstracts, 'categories' : categories})
df.head()

id                                              title  \
0  0712.1975         Reentrant spin glass transition in LuFe2O4   
1  0804.3104  Teichm\"uller Structures and Dual Geometric Gi...   
2  0810.3615  Exact results for the Wigner transform phase s...   
3  0810.5491  Nonequilibrium phase transition in a spreading...   
4  0902.3288  Origin and evolution of cosmic accelerators - ...   

                                            abstract  \
0    We have carried out a comprehensive investig...   
1    The Gibbs measure theory for smooth potentia...   
2    Closed form analytical expressions are obtai...   
3    We consider a nonequilibrium process on a ti...   
4    One of the most tantalizing questions in ast...   

                          categories  
0  cond-mat.str-el cond-mat.mtrl-sci  
1                    math.DS math.CV  
2                    physics.atom-ph  
3                 cond-mat.stat-mech  
4            astro-ph.CO astro-ph.HE

In [9]:
ml_df = df[df['categories'].str.contains("cs.LG")]

sentencesList= ml_df['abstract'].tolist()

In [10]:
print(len(ml_df))

1494


In [11]:
print(sentencesList[0])

  The extraction and understanding of temporal events and their relations are
major challenges in natural language processing. Processing text on a
sentence-by-sentence or expression-by-expression basis often fails, in part due
to the challenge of capturing the global consistency of the text. We present an
ensemble method, which reconciles the outputs of multiple classifiers of
temporal expressions across the text using integer programming. Computational
experiments show that the ensemble improves upon the best individual results
from two recent challenges, SemEval-2013 TempEval-3 (Temporal Annotation) and
SemEval-2016 Task 12 (Clinical TempEval).



In [12]:
ml_df.iloc[1]['id']

'1611.10351'

In [13]:
import time
start_time = time.time()
embeddings = model.encode(sentencesList, convert_to_tensor=True)
end_time = time.time()
print("Time for computing embeddings:"+ str(end_time-start_time) )

Batches:   0%|          | 0/47 [00:00<?, ?it/s]

Time for computing embeddings:771.5063283443451


In [14]:
print(np.shape(embeddings))

torch.Size([1494, 768])


In [15]:
cosine_scores = util.pytorch_cos_sim(embeddings, embeddings)

In [16]:
count = 0
for scores in cosine_scores:
    scores[count]=0.0
    max_elements, max_indices = torch.max(scores,dim=0)
    max_index = max_indices.item()
    print("\n*********\n")
    print("**Paper Id :"+ml_df.iloc[count]['id']+' '+'\nTitle :'+ml_df.iloc[count]['title']
          +'\n'+ml_df.iloc[count]['abstract']+
          '\n**Paper Id :' +ml_df.iloc[max_index]['id']+' '+'\nTitle :'+
          ml_df.iloc[max_index]['title']+'\n'+
          ml_df.iloc[max_index]['abstract'])
    count =count+1


*********

**Paper Id :1412.1866 
Title :Integer-Programming Ensemble of Temporal-Relations Classifiers
  The extraction and understanding of temporal events and their relations are
major challenges in natural language processing. Processing text on a
sentence-by-sentence or expression-by-expression basis often fails, in part due
to the challenge of capturing the global consistency of the text. We present an
ensemble method, which reconciles the outputs of multiple classifiers of
temporal expressions across the text using integer programming. Computational
experiments show that the ensemble improves upon the best individual results
from two recent challenges, SemEval-2013 TempEval-3 (Temporal Annotation) and
SemEval-2016 Task 12 (Clinical TempEval).

**Paper Id :1908.07018 
Title :Tale of tails using rule augmented sequence labeling for event
  extraction
  The problem of event extraction is a relatively difficult task for low
resource languages due to the non-availability of sufficie

In [17]:
print(len(embeddings))

1494


In [18]:
print(np.shape(embeddings))

torch.Size([1494, 768])


In [19]:
print(np.shape(cosine_scores))

torch.Size([1494, 1494])
